# Filter the person annotations

In [1]:
import json

In [2]:
json_file = open('../../workspace/annotations/json/train.json')
data = json.load(json_file)

In [3]:
data['categories']

[{'supercategory': 'person', 'id': 1, 'name': 'person'},
 {'supercategory': 'vehicle', 'id': 2, 'name': 'bicycle'},
 {'supercategory': 'vehicle', 'id': 3, 'name': 'car'},
 {'supercategory': 'vehicle', 'id': 4, 'name': 'motorcycle'},
 {'supercategory': 'vehicle', 'id': 5, 'name': 'airplane'},
 {'supercategory': 'vehicle', 'id': 6, 'name': 'bus'},
 {'supercategory': 'vehicle', 'id': 7, 'name': 'train'},
 {'supercategory': 'vehicle', 'id': 8, 'name': 'truck'},
 {'supercategory': 'vehicle', 'id': 9, 'name': 'boat'},
 {'supercategory': 'outdoor', 'id': 10, 'name': 'traffic light'},
 {'supercategory': 'outdoor', 'id': 11, 'name': 'fire hydrant'},
 {'supercategory': 'outdoor', 'id': 13, 'name': 'stop sign'},
 {'supercategory': 'outdoor', 'id': 14, 'name': 'parking meter'},
 {'supercategory': 'outdoor', 'id': 15, 'name': 'bench'},
 {'supercategory': 'animal', 'id': 16, 'name': 'bird'},
 {'supercategory': 'animal', 'id': 17, 'name': 'cat'},
 {'supercategory': 'animal', 'id': 18, 'name': 'dog'},

In [4]:
person_annotations = [obj for obj in data['annotations'] if obj['category_id'] == 1]

In [5]:
person_annotations

[{'segmentation': [[329.88,
    211.23,
    337.63,
    211.93,
    341.51,
    210.17,
    341.86,
    206.65,
    340.1,
    202.77,
    335.52,
    199.6,
    335.52,
    197.13,
    335.52,
    190.44,
    339.04,
    186.21,
    342.57,
    170.35,
    345.74,
    159.43,
    342.57,
    154.14,
    340.1,
    148.86,
    336.93,
    143.92,
    337.28,
    138.28,
    344.68,
    138.28,
    340.45,
    122.43,
    339.75,
    116.79,
    334.46,
    107.63,
    320.37,
    104.1,
    325.65,
    97.06,
    326.0,
    91.06,
    321.77,
    82.25,
    316.49,
    89.66,
    305.21,
    87.19,
    304.51,
    92.47,
    304.16,
    97.06,
    305.21,
    100.58,
    304.16,
    103.4,
    292.53,
    105.51,
    284.42,
    123.84,
    278.43,
    140.05,
    273.14,
    146.74,
    273.85,
    152.73,
    279.49,
    156.26,
    281.6,
    154.14,
    284.07,
    144.63,
    289.0,
    133.0,
    293.23,
    133.7,
    294.99,
    125.95,
    295.35,
    157.67,
    312.26,
    1

# Mege image with annotation

# Converting to TFRecords

In [7]:
import os
import io
import tensorflow as tf
import tensorflow.compat.v1 as tf
from object_detection.utils import dataset_util

def create_tf_example(width, height, path, filename, id):
    with tf.gfile.GFile(os.path.join(path, '{}'.format(filename)), 'rb') as fid:
        encoded_jpg = fid.read()
    encoded_jpg_io = io.BytesIO(encoded_jpg)

    filename = filename.encode('utf8')
    image_format = b'jpg'
    xmins = []
    xmaxs = []
    ymins = []
    ymaxs = []
    classes_text = []
    classes = []
    
    image_annoations = [x for x in person_annotations if x['image_id'] == id]

    for anno in image_annoations:
        xmins.append(anno['bbox'][0] / width)
        xmaxs.append(anno['bbox'][1] / width)
        ymins.append(anno['bbox'][2] / height)
        ymaxs.append(anno['bbox'][3] / height)
        classes_text.append('person'.encode('utf8'))
        classes.append(1)

    tf_example = tf.train.Example(features=tf.train.Features(feature={
        'image/height': dataset_util.int64_feature(height),
        'image/width': dataset_util.int64_feature(width),
        'image/filename': dataset_util.bytes_feature(filename),
        'image/source_id': dataset_util.bytes_feature(filename),
        'image/encoded': dataset_util.bytes_feature(encoded_jpg),
        'image/format': dataset_util.bytes_feature(image_format),
        'image/object/bbox/xmin': dataset_util.float_list_feature(xmins),
        'image/object/bbox/xmax': dataset_util.float_list_feature(xmaxs),
        'image/object/bbox/ymin': dataset_util.float_list_feature(ymins),
        'image/object/bbox/ymax': dataset_util.float_list_feature(ymaxs),
        'image/object/class/text': dataset_util.bytes_list_feature(classes_text),
        'image/object/class/label': dataset_util.int64_list_feature(classes),
    }))
    
    return tf_example

writer = tf.python_io.TFRecordWriter('../../workspace/annotations/test.record')

count = 0
length = len(data['images'])

for image in data['images']:
    tf_example = create_tf_example(image['width'], image['height'], '../../workspace/images/train/', image['file_name'], image['id'])
    writer.write(tf_example.SerializeToString())
    count += 1
    print('' + str(count) + ' / ' + str(length))
    
writer.close()

1 / 82783
2 / 82783
3 / 82783
4 / 82783
5 / 82783
6 / 82783
7 / 82783
8 / 82783
9 / 82783
10 / 82783
11 / 82783
12 / 82783
13 / 82783
14 / 82783
15 / 82783
16 / 82783
17 / 82783
18 / 82783
19 / 82783
20 / 82783
21 / 82783
22 / 82783
23 / 82783
24 / 82783
25 / 82783
26 / 82783
27 / 82783
28 / 82783
29 / 82783
30 / 82783
31 / 82783
32 / 82783
33 / 82783
34 / 82783
35 / 82783
36 / 82783
37 / 82783
38 / 82783
39 / 82783
40 / 82783
41 / 82783
42 / 82783
43 / 82783
44 / 82783
45 / 82783
46 / 82783
47 / 82783
48 / 82783
49 / 82783
50 / 82783
51 / 82783
52 / 82783
53 / 82783
54 / 82783
55 / 82783
56 / 82783
57 / 82783
58 / 82783
59 / 82783
60 / 82783
61 / 82783
62 / 82783
63 / 82783
64 / 82783
65 / 82783
66 / 82783
67 / 82783
68 / 82783
69 / 82783
70 / 82783
71 / 82783
72 / 82783
73 / 82783
74 / 82783
75 / 82783
76 / 82783
77 / 82783
78 / 82783
79 / 82783
80 / 82783
81 / 82783
82 / 82783
83 / 82783
84 / 82783
85 / 82783
86 / 82783
87 / 82783
88 / 82783
89 / 82783
90 / 82783
91 / 82783
92 / 827

697 / 82783
698 / 82783
699 / 82783
700 / 82783
701 / 82783
702 / 82783
703 / 82783
704 / 82783
705 / 82783
706 / 82783
707 / 82783
708 / 82783
709 / 82783
710 / 82783
711 / 82783
712 / 82783
713 / 82783
714 / 82783
715 / 82783
716 / 82783
717 / 82783
718 / 82783
719 / 82783
720 / 82783
721 / 82783
722 / 82783
723 / 82783
724 / 82783
725 / 82783
726 / 82783
727 / 82783
728 / 82783
729 / 82783
730 / 82783
731 / 82783
732 / 82783
733 / 82783
734 / 82783
735 / 82783
736 / 82783
737 / 82783
738 / 82783
739 / 82783
740 / 82783
741 / 82783
742 / 82783
743 / 82783
744 / 82783
745 / 82783
746 / 82783
747 / 82783
748 / 82783
749 / 82783
750 / 82783
751 / 82783
752 / 82783
753 / 82783
754 / 82783
755 / 82783
756 / 82783
757 / 82783
758 / 82783
759 / 82783
760 / 82783
761 / 82783
762 / 82783
763 / 82783
764 / 82783
765 / 82783
766 / 82783
767 / 82783
768 / 82783
769 / 82783
770 / 82783
771 / 82783
772 / 82783
773 / 82783
774 / 82783
775 / 82783
776 / 82783
777 / 82783
778 / 82783
779 / 82783
780 

1352 / 82783
1353 / 82783
1354 / 82783
1355 / 82783
1356 / 82783
1357 / 82783
1358 / 82783
1359 / 82783
1360 / 82783
1361 / 82783
1362 / 82783
1363 / 82783
1364 / 82783
1365 / 82783
1366 / 82783
1367 / 82783
1368 / 82783
1369 / 82783
1370 / 82783
1371 / 82783
1372 / 82783
1373 / 82783
1374 / 82783
1375 / 82783
1376 / 82783
1377 / 82783
1378 / 82783
1379 / 82783
1380 / 82783
1381 / 82783
1382 / 82783
1383 / 82783
1384 / 82783
1385 / 82783
1386 / 82783
1387 / 82783
1388 / 82783
1389 / 82783
1390 / 82783
1391 / 82783
1392 / 82783
1393 / 82783
1394 / 82783
1395 / 82783
1396 / 82783
1397 / 82783
1398 / 82783
1399 / 82783
1400 / 82783
1401 / 82783
1402 / 82783
1403 / 82783
1404 / 82783
1405 / 82783
1406 / 82783
1407 / 82783
1408 / 82783
1409 / 82783
1410 / 82783
1411 / 82783
1412 / 82783
1413 / 82783
1414 / 82783
1415 / 82783
1416 / 82783
1417 / 82783
1418 / 82783
1419 / 82783
1420 / 82783
1421 / 82783
1422 / 82783
1423 / 82783
1424 / 82783
1425 / 82783
1426 / 82783
1427 / 82783
1428 / 82783

1985 / 82783
1986 / 82783
1987 / 82783
1988 / 82783
1989 / 82783
1990 / 82783
1991 / 82783
1992 / 82783
1993 / 82783
1994 / 82783
1995 / 82783
1996 / 82783
1997 / 82783
1998 / 82783
1999 / 82783
2000 / 82783
2001 / 82783
2002 / 82783
2003 / 82783
2004 / 82783
2005 / 82783
2006 / 82783
2007 / 82783
2008 / 82783
2009 / 82783
2010 / 82783
2011 / 82783
2012 / 82783
2013 / 82783
2014 / 82783
2015 / 82783
2016 / 82783
2017 / 82783
2018 / 82783
2019 / 82783
2020 / 82783
2021 / 82783
2022 / 82783
2023 / 82783
2024 / 82783
2025 / 82783
2026 / 82783
2027 / 82783
2028 / 82783
2029 / 82783
2030 / 82783
2031 / 82783
2032 / 82783
2033 / 82783
2034 / 82783
2035 / 82783
2036 / 82783
2037 / 82783
2038 / 82783
2039 / 82783
2040 / 82783
2041 / 82783
2042 / 82783
2043 / 82783
2044 / 82783
2045 / 82783
2046 / 82783
2047 / 82783
2048 / 82783
2049 / 82783
2050 / 82783
2051 / 82783
2052 / 82783
2053 / 82783
2054 / 82783
2055 / 82783
2056 / 82783
2057 / 82783
2058 / 82783
2059 / 82783
2060 / 82783
2061 / 82783

2618 / 82783
2619 / 82783
2620 / 82783
2621 / 82783
2622 / 82783
2623 / 82783
2624 / 82783
2625 / 82783
2626 / 82783
2627 / 82783
2628 / 82783
2629 / 82783
2630 / 82783
2631 / 82783
2632 / 82783
2633 / 82783
2634 / 82783
2635 / 82783
2636 / 82783
2637 / 82783
2638 / 82783
2639 / 82783
2640 / 82783
2641 / 82783
2642 / 82783
2643 / 82783
2644 / 82783
2645 / 82783
2646 / 82783
2647 / 82783
2648 / 82783
2649 / 82783
2650 / 82783
2651 / 82783
2652 / 82783
2653 / 82783
2654 / 82783
2655 / 82783
2656 / 82783
2657 / 82783
2658 / 82783
2659 / 82783
2660 / 82783
2661 / 82783
2662 / 82783
2663 / 82783
2664 / 82783
2665 / 82783
2666 / 82783
2667 / 82783
2668 / 82783
2669 / 82783
2670 / 82783
2671 / 82783
2672 / 82783
2673 / 82783
2674 / 82783
2675 / 82783
2676 / 82783
2677 / 82783
2678 / 82783
2679 / 82783
2680 / 82783
2681 / 82783
2682 / 82783
2683 / 82783
2684 / 82783
2685 / 82783
2686 / 82783
2687 / 82783
2688 / 82783
2689 / 82783
2690 / 82783
2691 / 82783
2692 / 82783
2693 / 82783
2694 / 82783

...

80017 / 82783
80018 / 82783
80019 / 82783
80020 / 82783
80021 / 82783
80022 / 82783
80023 / 82783
80024 / 82783
80025 / 82783
80026 / 82783
80027 / 82783
80028 / 82783
80029 / 82783
80030 / 82783
80031 / 82783
80032 / 82783
80033 / 82783
80034 / 82783
80035 / 82783
80036 / 82783
80037 / 82783
80038 / 82783
80039 / 82783
80040 / 82783
80041 / 82783
80042 / 82783
80043 / 82783
80044 / 82783
80045 / 82783
80046 / 82783
80047 / 82783
80048 / 82783
80049 / 82783
80050 / 82783
80051 / 82783
80052 / 82783
80053 / 82783
80054 / 82783
80055 / 82783
80056 / 82783
80057 / 82783
80058 / 82783
80059 / 82783
80060 / 82783
80061 / 82783
80062 / 82783
80063 / 82783
80064 / 82783
80065 / 82783
80066 / 82783
80067 / 82783
80068 / 82783
80069 / 82783
80070 / 82783
80071 / 82783
80072 / 82783
80073 / 82783
80074 / 82783
80075 / 82783
80076 / 82783
80077 / 82783
80078 / 82783
80079 / 82783
80080 / 82783
80081 / 82783
80082 / 82783
80083 / 82783
80084 / 82783
80085 / 82783
80086 / 82783
80087 / 82783
80088 

80602 / 82783
80603 / 82783
80604 / 82783
80605 / 82783
80606 / 82783
80607 / 82783
80608 / 82783
80609 / 82783
80610 / 82783
80611 / 82783
80612 / 82783
80613 / 82783
80614 / 82783
80615 / 82783
80616 / 82783
80617 / 82783
80618 / 82783
80619 / 82783
80620 / 82783
80621 / 82783
80622 / 82783
80623 / 82783
80624 / 82783
80625 / 82783
80626 / 82783
80627 / 82783
80628 / 82783
80629 / 82783
80630 / 82783
80631 / 82783
80632 / 82783
80633 / 82783
80634 / 82783
80635 / 82783
80636 / 82783
80637 / 82783
80638 / 82783
80639 / 82783
80640 / 82783
80641 / 82783
80642 / 82783
80643 / 82783
80644 / 82783
80645 / 82783
80646 / 82783
80647 / 82783
80648 / 82783
80649 / 82783
80650 / 82783
80651 / 82783
80652 / 82783
80653 / 82783
80654 / 82783
80655 / 82783
80656 / 82783
80657 / 82783
80658 / 82783
80659 / 82783
80660 / 82783
80661 / 82783
80662 / 82783
80663 / 82783
80664 / 82783
80665 / 82783
80666 / 82783
80667 / 82783
80668 / 82783
80669 / 82783
80670 / 82783
80671 / 82783
80672 / 82783
80673 

81187 / 82783
81188 / 82783
81189 / 82783
81190 / 82783
81191 / 82783
81192 / 82783
81193 / 82783
81194 / 82783
81195 / 82783
81196 / 82783
81197 / 82783
81198 / 82783
81199 / 82783
81200 / 82783
81201 / 82783
81202 / 82783
81203 / 82783
81204 / 82783
81205 / 82783
81206 / 82783
81207 / 82783
81208 / 82783
81209 / 82783
81210 / 82783
81211 / 82783
81212 / 82783
81213 / 82783
81214 / 82783
81215 / 82783
81216 / 82783
81217 / 82783
81218 / 82783
81219 / 82783
81220 / 82783
81221 / 82783
81222 / 82783
81223 / 82783
81224 / 82783
81225 / 82783
81226 / 82783
81227 / 82783
81228 / 82783
81229 / 82783
81230 / 82783
81231 / 82783
81232 / 82783
81233 / 82783
81234 / 82783
81235 / 82783
81236 / 82783
81237 / 82783
81238 / 82783
81239 / 82783
81240 / 82783
81241 / 82783
81242 / 82783
81243 / 82783
81244 / 82783
81245 / 82783
81246 / 82783
81247 / 82783
81248 / 82783
81249 / 82783
81250 / 82783
81251 / 82783
81252 / 82783
81253 / 82783
81254 / 82783
81255 / 82783
81256 / 82783
81257 / 82783
81258 

81776 / 82783
81777 / 82783
81778 / 82783
81779 / 82783
81780 / 82783
81781 / 82783
81782 / 82783
81783 / 82783
81784 / 82783
81785 / 82783
81786 / 82783
81787 / 82783
81788 / 82783
81789 / 82783
81790 / 82783
81791 / 82783
81792 / 82783
81793 / 82783
81794 / 82783
81795 / 82783
81796 / 82783
81797 / 82783
81798 / 82783
81799 / 82783
81800 / 82783
81801 / 82783
81802 / 82783
81803 / 82783
81804 / 82783
81805 / 82783
81806 / 82783
81807 / 82783
81808 / 82783
81809 / 82783
81810 / 82783
81811 / 82783
81812 / 82783
81813 / 82783
81814 / 82783
81815 / 82783
81816 / 82783
81817 / 82783
81818 / 82783
81819 / 82783
81820 / 82783
81821 / 82783
81822 / 82783
81823 / 82783
81824 / 82783
81825 / 82783
81826 / 82783
81827 / 82783
81828 / 82783
81829 / 82783
81830 / 82783
81831 / 82783
81832 / 82783
81833 / 82783
81834 / 82783
81835 / 82783
81836 / 82783
81837 / 82783
81838 / 82783
81839 / 82783
81840 / 82783
81841 / 82783
81842 / 82783
81843 / 82783
81844 / 82783
81845 / 82783
81846 / 82783
81847 

82364 / 82783
82365 / 82783
82366 / 82783
82367 / 82783
82368 / 82783
82369 / 82783
82370 / 82783
82371 / 82783
82372 / 82783
82373 / 82783
82374 / 82783
82375 / 82783
82376 / 82783
82377 / 82783
82378 / 82783
82379 / 82783
82380 / 82783
82381 / 82783
82382 / 82783
82383 / 82783
82384 / 82783
82385 / 82783
82386 / 82783
82387 / 82783
82388 / 82783
82389 / 82783
82390 / 82783
82391 / 82783
82392 / 82783
82393 / 82783
82394 / 82783
82395 / 82783
82396 / 82783
82397 / 82783
82398 / 82783
82399 / 82783
82400 / 82783
82401 / 82783
82402 / 82783
82403 / 82783
82404 / 82783
82405 / 82783
82406 / 82783
82407 / 82783
82408 / 82783
82409 / 82783
82410 / 82783
82411 / 82783
82412 / 82783
82413 / 82783
82414 / 82783
82415 / 82783
82416 / 82783
82417 / 82783
82418 / 82783
82419 / 82783
82420 / 82783
82421 / 82783
82422 / 82783
82423 / 82783
82424 / 82783
82425 / 82783
82426 / 82783
82427 / 82783
82428 / 82783
82429 / 82783
82430 / 82783
82431 / 82783
82432 / 82783
82433 / 82783
82434 / 82783
82435 

In [13]:
img[0]

{'license': 5,
 'file_name': 'COCO_train2014_000000057870.jpg',
 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000057870.jpg',
 'height': 480,
 'width': 640,
 'date_captured': '2013-11-14 16:28:13',
 'flickr_url': 'http://farm4.staticflickr.com/3153/2970773875_164f0c0b83_z.jpg',
 'id': 57870}